<a name="top"></a>
<h1>Neighborhood Battle 2: The Notebook</h1>

<h2>Contents</h2>

1. [Introduction: Business Problem, Interested Audience](#introduction)
2. [Data: Forward Sortation Areas, Foursquare, Maps](#data)
    1. [Forward Sortation Areas (FSAs)](#neighborhoods)
    2. [Mapping FSAs](#mapping_neighborhoods)
    3. [Buffets and Restaurants with Foursquare API](#buffets_and_restaurants)
    4. [Mapping Restaurants](#mapping_restaurants)
    5. [Real Estate Heatmap](#real_estate)
3. [Methodology](#methodology)
    1. [Secondary Consideration: Competition](#competition)
    2. [Secondary Consideration: Price](#price)
4. [Results and Discussion](#results)
5. [Conclusion](#conclusion)

<a name="introduction"></a>
<h2>Introduction: Business Problem, Interested Audience</h2>

Someone would like to open a new **buffet restaurant** in **Toronto, Ontario, Canada**.

They do not want to have too much competition in the new area primarily in the way of **other buffet restaurants** nearby. Other possible considerations are the **number of other restaurants of any kind** nearby and the **cost of the area**.

The buffet restaurant **will** open but the location is not yet decided.

***Business Problem***: Where in Toronto should the new buffet restaurant be located? To be determined!

***Interested Audience***: Who wants to open a buffet restaurant? Our imaginary future buffet owner!

***Primary Consideration***: Are there other buffet restaurants nearby? To be determined!

***Secondary Consideration***: How many other restaurants are nearby? To be determined!

***Secondary Consideration***: How much would it be to open in that location? To be determined!

**This will not find an exact location but provide recommendation for possible locations.**

[To Top](#top)
<a name="data"></a>
<h2>Data: Forward Sortation Areas, Foursquare, Maps</h2>

We have primary and secondary considerations that will help guide our final recommendation. We will use various pieces of data to address each one.

***Primary Consideration***: Are there other buffet restaurants nearby? We do not want any buffet restaurants.

The **Foursquare API** will give us information about the buffets in the city of Toronto.

***Secondary Consideration***: How many other restaurants are nearby? We are okay with some competition but not too much in relative comparison to highest possible competition in Toronto.

The **Foursquare API** will give us information about the restaurants in the city of Toronto.

***Secondary Consideration***: How much would it be to open in that location? The buffet will open but if possible, a cheaper location is better.

A **Folium map** will be created with data returned from the **Foursquare API** and a pre-existing **csv file**. The data in the csv file can also be acquired using **geocoder** if so desired. A second pre-existing **heatmap of real estate pricing in Toronto** from https://www.canadianbusiness.com/blogs-and-comment/check-out-this-heat-map-of-toronto-real-estate-prices/ will be compared against the created Folium map.

We'll start with installing and importing everything that we know we will be using. We can add other things in later on down if we find we need to though. This first part of installing geopy and Folium can take a while so once it's been done the first time, we can comment it out to make things go by more quickly.

In [1]:
#!pip install geopy
#!pip install Folium

In [2]:
import pandas as pd
import requests #used to handle requests such as those used to get tables from the web
import numpy as np
import folium

from geopy.geocoders import Nominatim #convert street addresses into latitude and longitude

#used to handle json files such as those returned by the Foursquare API
import json
from pandas.io.json import json_normalize

#matplotlib and modules
import matplotlib.cm as cm
import matplotlib.colors as colors

print('Importing done!')

Importing done!


[To Top](#top)
<a name="neighborhoods"></a>
<h3>Forward Sortation Areas (FSAs)</h3>

The desired area is a Forward Sortation Area in Toronto, Ontario, Canada. An FSA is linked to a postcode and is a smaller area within the larger city. With that being the case, we should get an idea of where the FSAs are located. We will use almost the exact same code as a previous project for this portion as well as some of the same descriptions.

We'll first connect to the webpage containing the postal information that we need. Upon examining the webpage, we notice that there are actually three tables but we only need one of them, the very first one. Once we pull out the table we want, we can get to work on preparing the table in the way of the neighborhood and borough columns being removed or assigned values. When removing the rows, we also want to be careful and reset the index. Neighborhoods that share the same postcode are also combined into one row.

Note that combining the neighborhoods based on postcode makes it so that we're really looking at each postcode or FSA. For the purposes of this notebook and project, these postcode areas and the neighborhoods will be considered interchangeable unless otherwise stated.

In [3]:
#whoa, I can see everything now!
pd.set_option('display.max_rows', None)

In [4]:
#get table of Toronto postal codes
url = 'https://en.wikipedia.org/wiki/List_of_postal_codes_of_Canada:_M'
n_url = requests.get(url)
list_tables = pd.read_html(n_url.text)
postal_table = list_tables[0]
postal_table.rename(columns={"Neighbourhood":"Neighborhood"}, inplace=True)

#clean table of Toronto postal codes
for i in range(len(postal_table)-1):
    if postal_table['Neighborhood'][i] == 'Not assigned':
        postal_table['Neighborhood'][i] = postal_table['Borough'][i]

postal_table = postal_table[postal_table.Borough != 'Not assigned']
postal_table_indexed = postal_table.reset_index(drop=True)
postal_table_sorted = postal_table_indexed.sort_values(by=['Postcode'])

#combine Neighborhoods that share the same Postcode
for i in range(len(postal_table_sorted)-1):
    if postal_table_sorted['Postcode'][i] == postal_table_sorted['Postcode'][i+1]:
        postal_table_sorted['Neighborhood'][i+1] = (postal_table_sorted['Neighborhood'][i] + ', ' + postal_table_sorted['Neighborhood'][i+1])
        postal_table_sorted.drop([i], inplace=True)

postal_table_combined = postal_table_sorted
postal_table_combined = postal_table_combined.reset_index(drop=True)

#get and add latitude and longitude data for each Postcode in postal_table_combined
coord = pd.read_csv('Geospatial_Coordinates.csv')
coord.rename(columns={"Postal Code":"Postcode"}, inplace=True)
postal_table_coord = postal_table_combined.join(coord.set_index('Postcode'), on='Postcode')

postal_table_coord

Postcode           Borough  \
0        M1B       Scarborough   
1        M1C       Scarborough   
2        M1E       Scarborough   
3        M1G       Scarborough   
4        M1H       Scarborough   
5        M1J       Scarborough   
6        M1K       Scarborough   
7        M1L       Scarborough   
8        M1M       Scarborough   
9        M1N       Scarborough   
10       M1P       Scarborough   
11       M1R       Scarborough   
12       M1S       Scarborough   
13       M1T       Scarborough   
14       M1V       Scarborough   
15       M1W       Scarborough   
16       M1X       Scarborough   
17       M2H        North York   
18       M2J        North York   
19       M2K        North York   
20       M2L        North York   
21       M2M        North York   
22       M2N        North York   
23       M2P        North York   
24       M2R        North York   
25       M3A        North York   
26       M3B        North York   
27       M3C        North York   
28       M3H        North York   
29       M3J        North York   
30       M3K        North York   
31       M3L        North York   
32       M3M        North York   
33       M3N        North York   
34       M4A        North York   
35       M4B         East York   
36       M4C         East York   
37       M4E      East Toronto   
38       M4G         East York   
39       M4H         East York   
40       M4J         East York   
41       M4K      East Toronto   
42       M4L      East Toronto   
43       M4M      East Toronto   
44       M4N   Central Toronto   
45       M4P   Central Toronto   
46       M4R   Central Toronto   
47       M4S   Central Toronto   
48       M4T   Central Toronto   
49       M4V   Central Toronto   
50       M4W  Downtown Toronto   
51       M4X  Downtown Toronto   
52       M4Y  Downtown Toronto   
53       M5A  Downtown Toronto   
54       M5B  Downtown Toronto   
55       M5C  Downtown Toronto   
56       M5E  Downtown Toronto   
57       M5G  Downtown Toronto   
58       M5H  Downtown Toronto   
59       M5J  Downtown Toronto   
60       M5K  Downtown Toronto   
61       M5L  Downtown Toronto   
62       M5M        North York   
63       M5N   Central Toronto   
64       M5P   Central Toronto   
65       M5R   Central Toronto   
66       M5S  Downtown Toronto   
67       M5T  Downtown Toronto   
68       M5V  Downtown Toronto   
69       M5W  Downtown Toronto   
70       M5X  Downtown Toronto   
71       M6A        North York   
72       M6B        North York   
73       M6C              York   
74       M6E              York   
75       M6G  Downtown Toronto   
76       M6H      West Toronto   
77       M6J      West Toronto   
78       M6K      West Toronto   
79       M6L        North York   
80       M6M              York   
81       M6N              York   
82       M6P      West Toronto   
83       M6R      West Toronto   
84       M6S      West Toronto   
85       M7A      Queen's Park   
86       M7R       Mississauga   
87       M7Y      East Toronto   
88       M8V         Etobicoke   
89       M8W         Etobicoke   
90       M8X         Etobicoke   
91       M8Y         Etobicoke   
92       M8Z         Etobicoke   
93       M9A  Downtown Toronto   
94       M9B         Etobicoke   
95       M9C         Etobicoke   
96       M9L        North York   
97       M9M        North York   
98       M9N              York   
99       M9P         Etobicoke   
100      M9R         Etobicoke   
101      M9V         Etobicoke   
102      M9W         Etobicoke   

                                          Neighborhood   Latitude  Longitude  
0                                       Rouge, Malvern  43.806686 -79.194353  
1               Highland Creek, Rouge Hill, Port Union  43.784535 -79.160497  
2                    Guildwood, Morningside, West Hill  43.763573 -79.188711  
3                                               Woburn  43.770992 -79.216917  
4                                            Cedarbrae  43.773136 -79.23

[To Top](#top)
<a name="mapping_neighborhoods"></a>
<h3>Mapping FSAs</h3>

We will use Folium to create a visual representation of these FSAs. We know the name of our city but we need its geographical coordinates.

In [5]:
#define chosen city
address = 'Toronto, ON, Canada'

#get latitude and longitude for chosen city
geolocator = Nominatim(user_agent="explorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geographic coordinates of Toronto, Ontario, Canada are Latitude: {}, Longitude: {}.'.format(latitude, longitude))

The geographic coordinates of Toronto, Ontario, Canada are Latitude: 43.653963, Longitude: -79.387207.


The geographical coordinates are now defined. Combined with the data of our neighborhoods, we have most of what we need to begin mapping with Folium. We do need to define a few more parameters such as our starting zoom level (zoom_start) and what kind of labels we want but that's not really something to worry too much about.

Note that this first map is not necessary but I believe it is helpful to see where the neighborhoods (really FSAs) are and get an idea of what the overall area looks like.

In [6]:
#create a Folium map of Toronto with neighborhoods marked
toronto_map = folium.Map(location=[latitude, longitude], zoom_start=10)

for postcode, latitude, longitude, borough, neighbourhood in zip(postal_table_coord['Postcode'], postal_table_coord['Latitude'], postal_table_coord['Longitude'], postal_table_coord['Borough'], postal_table_coord['Neighborhood']):
    label = '{}, {}, {}'.format(postcode, neighbourhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [latitude, longitude],
        radius=5,
        popup=label,
        color='gray',
        fill=True,
        fill_color='gray',
        fill_opacity=0.8,
        parse_html=False).add_to(toronto_map)  
    
toronto_map

**FSA Markers**: https://i.imgur.com/i4DadRY.jpg

[To Top](#top)
<a name="data"></a>
<a name="buffets_and_restaurants"></a>
<h3>Buffets and Restaurants with Foursquare API</h3>

***Primary Consideration***: Are there other buffet restaurants nearby?

***Secondary Consideration***: How many other restaurants are nearby?

Both of these considerations will be addressed through the use of the Foursquare API. In order to make our calls to Foursquare, we'll need our credentials and the version of the API we want to use. Note that the version is a string of numbers which actually represents a date in YYYYMMDD format. If so desired, the version can be changed to an earlier or a later date.

In [7]:
#Foursquare credentials, required to make calls to Foursquare API
CLIENT_ID = 'QS5G2JB5AQAWPY0ASRDOFWRPKIYAYY2U544P4CZFTHJJINBU'
CLIENT_SECRET = 'S5C2XZ3M2IDHTCMS3ZGUERP33G2PG0PXQKO04CWL55DXQXSG'
VERSION = '20180605'

In [8]:
radius = 500 #radius is in meters
LIMIT = 100

The following is a test call to Foursquare. Foursquare returns data as json files and many such files can contain a lot of information about one entry. It's a good idea to see what the returned data looks like so we know what we need to do later.

In [9]:
lat = postal_table_coord['Latitude'][0]
lng = postal_table_coord['Longitude'][0]
search_query = 'food'

      #'https://api.foursquare.com/v2/venues/search?client_id={}&client_secret={}&ll={},{}&v={}&query={}&radius={}&limit={}'

url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&query={}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng,
            search_query,
            radius, 
            LIMIT)

test_results = requests.get(url).json()

test_results

{'meta': {'code': 200, 'requestId': '5dfedc8995feaf001be9e959'},
 'response': {'warning': {'text': 'There aren\'t a lot of results for "food." Try something more general, reset your filters, or expand the search area.'},
  'headerLocation': 'Malvern',
  'headerFullLocation': 'Malvern, Toronto',
  'headerLocationGranularity': 'neighborhood',
  'query': 'food',
  'totalResults': 2,
  'suggestedBounds': {'ne': {'lat': 43.8111863045, 'lng': -79.18812958073042},
   'sw': {'lat': 43.80218629549999, 'lng': -79.2005772192696}},
  'groups': [{'type': 'Recommended Places',
    'name': 'recommended',
    'items': [{'reasons': {'count': 0,
       'items': [{'summary': 'This spot is popular',
         'type': 'general',
         'reasonName': 'globalInteractionReason'}]},
      'venue': {'id': '4bb6b9446edc76b0d771311c',
       'name': "Wendy's",
       'location': {'crossStreet': 'Morningside & Sheppard',
        'lat': 43.80744841934756,
        'lng': -79.19905558052072,
        'labeledLatLngs'

That's a lot of information! Some cutting down is in order here.

In [10]:
test_venues = test_results['response']['groups'][0]['items']

test_venues

[{'reasons': {'count': 0,
   'items': [{'summary': 'This spot is popular',
     'type': 'general',
     'reasonName': 'globalInteractionReason'}]},
  'venue': {'id': '4bb6b9446edc76b0d771311c',
   'name': "Wendy's",
   'location': {'crossStreet': 'Morningside & Sheppard',
    'lat': 43.80744841934756,
    'lng': -79.19905558052072,
    'labeledLatLngs': [{'label': 'display',
      'lat': 43.80744841934756,
      'lng': -79.19905558052072}],
    'distance': 387,
    'cc': 'CA',
    'city': 'Toronto',
    'state': 'ON',
    'country': 'Canada',
    'formattedAddress': ['Toronto ON', 'Canada']},
   'categories': [{'id': '4bf58dd8d48988d16e941735',
     'name': 'Fast Food Restaurant',
     'pluralName': 'Fast Food Restaurants',
     'shortName': 'Fast Food',
     'icon': {'prefix': 'https://ss3.4sqi.net/img/categories_v2/food/fastfood_',
      'suffix': '.png'},
     'primary': True}],
   'photos': {'count': 0, 'groups': []}},
  'referralId': 'e-0-4bb6b9446edc76b0d771311c-0'},
 {'reasons':

Cut Down! It still looks a little too unwieldy though. Cut Down 2: The Sequel is coming soon though! As we can see, we havea lot of information coming from one call and we have many calls that we need to make. Doing them one by one isn't something to look forward to. Luckily, we can use functions help us out.

Note that these functions are near identical to each other. A question might be why we have two separate functions that look almost the same. The short of it is that we want one for buffets and one for all restaurants.

Another note is the term used for the search_query in each. Buffet and Food are listed as venue categories on the Foursquare developer resources doc. Buffets are categorized as part of Food. This doc can be found at https://developer.foursquare.com/docs/resources/categories.

In [11]:
#function to get buffets
def getNearbyBuffets(postcodes, names, latitudes, longitudes, search_query = 'buffet', radius = 500):
    
    buffets_list = []
    for code, name, lat, lng in zip(postcodes, names, latitudes, longitudes):
            
        url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&query={}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng,
            search_query,
            radius, 
            LIMIT)
            
        results = requests.get(url).json()['response']['groups'][0]['items']
        
        buffets_list.append([(
            code,
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for buffet_list in buffets_list for item in buffet_list])
    nearby_venues.columns = ['Postcode',
                             'Neighborhood',
                             'Neighborhood Latitude',
                             'Neighborhood Longitude',
                             'Venue',
                             'Venue Latitude',
                             'Venue Longitude',
                             'Venue Category']
    
    return(nearby_venues)

The differences between these two functions are the search_query, the name of the list, and the name of the function.

In [12]:
#function to get restaurants in general
def getNearbyRestaurants(postcodes, names, latitudes, longitudes, search_query = 'food', radius = 500):
    
    venues_list = []
    for code, name, lat, lng in zip(postcodes, names, latitudes, longitudes):
            
        url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&v={}&ll={},{}&query={}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng,
            search_query,
            radius, 
            LIMIT)
            
        results = requests.get(url).json()['response']['groups'][0]['items']

        
        venues_list.append([(
            code,
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Postcode',
                             'Neighborhood',
                             'Neighborhood Latitude',
                             'Neighborhood Longitude',
                             'Venue',
                             'Venue Latitude',
                             'Venue Longitude',
                             'Venue Category']
    
    return(nearby_venues)

We have some functions but we have to remember to run them or they'll just sit there looking all nice and shiny.

In [15]:
#run buffet function
toronto_buffets = getNearbyBuffets(postcodes=postal_table_coord['Postcode'],
                                   names=postal_table_coord['Neighborhood'],
                                   latitudes=postal_table_coord['Latitude'],
                                   longitudes=postal_table_coord['Longitude']
                                  )

In [16]:
#run restaurant function
toronto_restaurants = getNearbyRestaurants(postcodes=postal_table_coord['Postcode'],
                                           names=postal_table_coord['Neighborhood'],
                                           latitudes=postal_table_coord['Latitude'],
                                           longitudes=postal_table_coord['Longitude']
                                  )

49 buffets in all of Toronto! Is that number high or low though?

In [17]:
print(toronto_buffets.shape)

(49, 8)


1672 restaurants in Toronto! Wow! 49 buffets out of 1672 restaurants seems like a good situtation for our future buffet owners!

In [18]:
print(toronto_restaurants.shape)

(1671, 8)


There are actually very few categorized strictly as buffet! It could be that this collection contains buffet-only establishments as well as general restaurants that have a buffet option.

In [19]:
toronto_buffets

Postcode                                       Neighborhood  \
0       M1P  Dorset Park, Scarborough Town Centre, Wexford ...   
1       M3C                   Flemingdon Park, Don Mills South   
2       M4G                                            Leaside   
3       M4K                       The Danforth West, Riverdale   
4       M4S                                         Davisville   
5       M4X                        Cabbagetown, St. James Town   
6       M4Y                               Church and Wellesley   
7       M4Y                               Church and Wellesley   
8       M5B                           Ryerson, Garden District   
9       M5B                           Ryerson, Garden District   
10      M5C                                     St. James Town   
11      M5C                                     St. James Town   
12      M5C                                     St. James Town   
13      M5C                                     St. James Town   
14      M5E                                        Berczy Park   
15      M5E                                        Berczy Park   
16      M5G                                 Central Bay Street   
17      M5G                                 Central Bay Street   
18      M5G                                 Central Bay Street   
19      M5H                           Adelaide, King, Richmond   
20      M5H                           Adelaide, King, Richmond   
21      M5H                           Adelaide, King, Richmond   
22      M5H                           Adelaide, King, Richmond   
23      M5K           Design Exchange, Toronto Dominion Centre   
24      M5K           Design Exchange, Toronto Dominion Centre   
25      M5K           Design Exchange, Toronto Dominion Centre   
26      M5K           Design Exchange, Toronto Dominion Centre   
27      M5K           Design Exchange, Toronto Dominion Centre   
28      M5K           Design Exchange, Toronto Dominion Centre   
29      M5K           Design Exchange, Toronto Dominion Centre   
30      M5L                     Commerce Court, Victoria Hotel   
31      M5L                     Commerce Court, Victoria Hotel   
32      M5L                     Commerce Court, Victoria Hotel   
33      M5L                     Commerce Court, Victoria Hotel   
34      M5L                     Commerce Court, Victoria Hotel   
35      M5S                     Harbord, University of Toronto   
36      M5T          Chinatown, Grange Park, Kensington Market   
37      M5W                    Stn A PO Boxes 25 The Esplanade   
38      M5W                    Stn A PO Boxes 25 The Esplanade   
39      M5W                    Stn A PO Boxes 25 The Esplanade   
40      M5X             First Canadian Place, Underground city   
41      M5X             First Canadian Place, Underground city   
42      M5X             First Canadian Place, Underground city   
43      M5X             First Canadian Place, Underground city   
44      M5X             First Canadian Place, Underground city   
45      M5X             First Canadian Place, Underground city   
46      M5X             First Canadian Place, Underground city   
47      M7A                                       Queen's Park   
48      M7A                                       Queen's Park   

    Neighborhood Latitude  Neighborhood Longitude  \
0               43.757410              -79.273304   
1               43.725900              -79.340923   
2               43.709060              -79.363452   
3               43.679557              -79.352188   
4               43.704324              -79.388790   
5               43.667967              -79.367675   
6               43.665860              -79.383160   
7               43.665860              -79.383160   
8               43.657162              -79.378937   
9               43.657162              -79.378937   
10              43.651494              -79.375418   
11              43.651494              -79.375418   
12           

In [20]:
toronto_restaurants

Postcode                                       Neighborhood  \
0         M1B                                     Rouge, Malvern   
1         M1B                                     Rouge, Malvern   
2         M1E                  Guildwood, Morningside, West Hill   
3         M1E                  Guildwood, Morningside, West Hill   
4         M1E                  Guildwood, Morningside, West Hill   
5         M1E                  Guildwood, Morningside, West Hill   
6         M1E                  Guildwood, Morningside, West Hill   
7         M1G                                             Woburn   
8         M1G                                             Woburn   
9         M1G                                             Woburn   
10        M1H                                          Cedarbrae   
11        M1H                                          Cedarbrae   
12        M1H                                          Cedarbrae   
13        M1H                                          Cedarbrae   
14        M1H                                          Cedarbrae   
15        M1J                                Scarborough Village   
16        M1K        East Birchmount Park, Ionview, Kennedy Park   
17        M1K        East Birchmount Park, Ionview, Kennedy Park   
18        M1K        East Birchmount Park, Ionview, Kennedy Park   
19        M1K        East Birchmount Park, Ionview, Kennedy Park   
20        M1L                    Clairlea, Golden Mile, Oakridge   
21        M1L                    Clairlea, Golden Mile, Oakridge   
22        M1L                    Clairlea, Golden Mile, Oakridge   
23        M1L                    Clairlea, Golden Mile, Oakridge   
24        M1M    Cliffcrest, Cliffside, Scarborough Village West   
25        M1N                        Birch Cliff, Cliffside West   
26        M1N                        Birch Cliff, Cliffside West   
27        M1P  Dorset Park, Scarborough Town Centre, Wexford ...   
28        M1P  Dorset Park, Scarborough Town Centre, Wexford ...   
29        M1P  Dorset Park, Scarborough Town Centre, Wexford ...   
30        M1P  Dorset Park, Scarborough Town Centre, Wexford ...   
31        M1R                                  Maryvale, Wexford   
32        M1R                                  Maryvale, Wexford   
33        M1R                                  Maryvale, Wexford   
34        M1R                                  Maryvale, Wexford   
35        M1R                                  Maryvale, Wexford   
36        M1R                                  Maryvale, Wexford   
37        M1S                                          Agincourt   
38        M1S                                          Agincourt   
39        M1S                                          Agincourt   
40        M1S                                          Agincourt   
41        M1T            Clarks Corners, Sullivan, Tam O'Shanter   
42        M1T            Clarks Corners, Sullivan, Tam O'Shanter   
43        M1T            Clarks Corners, Sullivan, Tam O'Shanter   
44        M1T            Clarks Corners, Sullivan, Tam O'Shanter   
45        M1T            Clarks Corners, Sullivan, Tam O'Shanter   
46        M1T            Clarks Corners, Sullivan, Tam O'Shanter   
47        M1T            Clarks Corners, Sullivan, Tam O'Shanter   
48        M1T            Clarks Corners, Sullivan, Tam O'Shanter   
49        M1V  Agincourt North, L'Amoreaux East, Milliken, St...   
50        M1V  Agincourt North, L'Amoreaux East, Milliken, St...   
51        M1W                                    L'Amoreaux West   
52        M1W                                    L'Amoreaux West   
53        M1W                                    L'Amoreaux West   
54        M1W                                    L'Amoreaux West   
55        M1W                                    L'Amoreaux West   
56        M1W                                    L'Amoreaux West   
57        M1W                                    L'Amoreaux W

Here we create copies of our dataframes. We're not doing anything with them that would warrant this but it sort of cuts down on typing the name out again. I could have chosen better names in the first place too. Now that I think about it, I think this actually resulted in more typing for me. How unfortunate!

In [21]:
tor_r = toronto_restaurants
tor_b = toronto_buffets

Foursquare lists buffets as a subcategory of food. There might be some overlap with some of toronto_buffets being inside toronto_restaurants. This concat will put the restaurants and buffets together and then drop anything that is identical. The new tor_g should now have no repeated entries. Interestingly, it comes out to 1651 rows from the initial 1672 for a difference of 21 instead of the expected 49.

In [22]:
tor_g = pd.concat([tor_r, tor_b, tor_b]).drop_duplicates(keep=False)

tor_g

Postcode                                       Neighborhood  \
0         M1B                                     Rouge, Malvern   
1         M1B                                     Rouge, Malvern   
2         M1E                  Guildwood, Morningside, West Hill   
3         M1E                  Guildwood, Morningside, West Hill   
4         M1E                  Guildwood, Morningside, West Hill   
5         M1E                  Guildwood, Morningside, West Hill   
6         M1E                  Guildwood, Morningside, West Hill   
7         M1G                                             Woburn   
8         M1G                                             Woburn   
9         M1G                                             Woburn   
10        M1H                                          Cedarbrae   
11        M1H                                          Cedarbrae   
12        M1H                                          Cedarbrae   
13        M1H                                          Cedarbrae   
14        M1H                                          Cedarbrae   
15        M1J                                Scarborough Village   
16        M1K        East Birchmount Park, Ionview, Kennedy Park   
17        M1K        East Birchmount Park, Ionview, Kennedy Park   
18        M1K        East Birchmount Park, Ionview, Kennedy Park   
19        M1K        East Birchmount Park, Ionview, Kennedy Park   
20        M1L                    Clairlea, Golden Mile, Oakridge   
21        M1L                    Clairlea, Golden Mile, Oakridge   
22        M1L                    Clairlea, Golden Mile, Oakridge   
23        M1L                    Clairlea, Golden Mile, Oakridge   
24        M1M    Cliffcrest, Cliffside, Scarborough Village West   
25        M1N                        Birch Cliff, Cliffside West   
26        M1N                        Birch Cliff, Cliffside West   
27        M1P  Dorset Park, Scarborough Town Centre, Wexford ...   
28        M1P  Dorset Park, Scarborough Town Centre, Wexford ...   
30        M1P  Dorset Park, Scarborough Town Centre, Wexford ...   
31        M1R                                  Maryvale, Wexford   
32        M1R                                  Maryvale, Wexford   
33        M1R                                  Maryvale, Wexford   
34        M1R                                  Maryvale, Wexford   
35        M1R                                  Maryvale, Wexford   
36        M1R                                  Maryvale, Wexford   
37        M1S                                          Agincourt   
38        M1S                                          Agincourt   
39        M1S                                          Agincourt   
40        M1S                                          Agincourt   
41        M1T            Clarks Corners, Sullivan, Tam O'Shanter   
42        M1T            Clarks Corners, Sullivan, Tam O'Shanter   
43        M1T            Clarks Corners, Sullivan, Tam O'Shanter   
44        M1T            Clarks Corners, Sullivan, Tam O'Shanter   
45        M1T            Clarks Corners, Sullivan, Tam O'Shanter   
46        M1T            Clarks Corners, Sullivan, Tam O'Shanter   
47        M1T            Clarks Corners, Sullivan, Tam O'Shanter   
48        M1T            Clarks Corners, Sullivan, Tam O'Shanter   
49        M1V  Agincourt North, L'Amoreaux East, Milliken, St...   
50        M1V  Agincourt North, L'Amoreaux East, Milliken, St...   
51        M1W                                    L'Amoreaux West   
52        M1W                                    L'Amoreaux West   
53        M1W                                    L'Amoreaux West   
54        M1W                                    L'Amoreaux West   
55        M1W                                    L'Amoreaux West   
56        M1W                                    L'Amoreaux West   
57        M1W                                    L'Amoreaux West   
58        M1W                                    L'Amoreaux W

In [23]:
print(tor_g.shape)

(1650, 8)


Let's see how many restaurants are in each neighborhood.

In [24]:
tor_g.groupby('Neighborhood').count()

Postcode  \
Neighborhood                                                   
Adelaide, King, Richmond                                  95   
Agincourt                                                  4   
Agincourt North, L'Amoreaux East, Milliken, Ste...         2   
Albion Gardens, Beaumond Heights, Humbergate, J...         5   
Alderwood, Long Branch                                     4   
Bathurst Manor, Downsview North, Wilson Heights            9   
Bayview Village                                            3   
Bedford Park, Lawrence Manor East                         20   
Berczy Park                                               50   
Birch Cliff, Cliffside West                                2   
Bloordale Gardens, Eringate, Markland Wood, Old...         3   
Brockton, Exhibition Place, Parkdale Village              14   
Business Reply Mail Processing Centre 969 Eastern          5   
CFB Toronto, Downsview East                                1   
CN Tower, Bathurst Quay, Island airport, Harbou...         2   
Cabbagetown, St. James Town                               29   
Caledonia-Fairbanks                                        1   
Canada Post Gateway Processing Centre                      6   
Cedarbrae                                                  5   
Central Bay Street                                        68   
Chinatown, Grange Park, Kensington Market                 57   
Christie                                                   7   
Church and Wellesley                                      64   
Clairlea, Golden Mile, Oakridge                            4   
Clarks Corners, Sullivan, Tam O'Shanter                    8   
Cliffcrest, Cliffside, Scarborough Village West            1   
Cloverdale, Islington, Martin Grove, Princess G...         1   
Commerce Court, Victoria Hotel                            98   
Davisville                                                30   
Davisville North                                           4   
Deer Park, Forest Hill SE, Rathnelly, South Hil...         9   
Del Ray, Keelesdale, Mount Dennis, Silverthorn             5   
Design Exchange, Toronto Dominion Centre                  97   
Don Mills North                                            4   
Dorset Park, Scarborough Town Centre, Wexford H...         3   
Dovercourt Village, Dufferin                               9   
Downsview Central                                          2   
Downsview, North Park, Upwood Park                         2   
East Birchmount Park, Ionview, Kennedy Park                4   
East Toronto                                               3   
Fairview, Henry Farm, Oriole                              28   
First Canadian Place, Underground city                    97   
Flemingdon Park, Don Mills South                           9   
Forest Hill North, Forest Hill West                        4   
Glencairn                                                  5   
Guildwood, Morningside, West Hill                          5   
Harbord, University of Toronto                            29   
Harbourfront                                              22   
Harbourfront East, Toronto Islands, Union Station         82   
High Park, The Junction South                             15   
Hillcrest Village                                          2   
Humber Bay Shores, Mimico South, New Toronto              11   
Humber Bay, King's Mill Park, Kingsway Park Sou...         2   
Humber Summit                                              4   
Kingsview Village, Martin Grove Gardens, Richvi...         1   
Kingsway Park South West, Mimico NW, The Queens...         5   
L'Amoreaux West                                           11   
Lawrence Heights, Lawrence Manor                           3   
Lawrence Park                                              1   
Leaside                                                   21   
Little Portugal, Trinity                                  45   
Maryvale, Wexford   

Grouping by Postcode presents a different view.

In [25]:
tor_g.groupby('Postcode').count()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  Venue  \
Postcode                                                                       
M1B                  2                      2                       2      2   
M1E                  5                      5                       5      5   
M1G                  3                      3                       3      3   
M1H                  5                      5                       5      5   
M1J                  1                      1                       1      1   
M1K                  4                      4                       4      4   
M1L                  4                      4                       4      4   
M1M                  1                      1                       1      1   
M1N                  2                      2                       2      2   
M1P                  3                      3                       3      3   
M1R                  6                      6                       6      6   
M1S                  4                      4                       4      4   
M1T                  8                      8                       8      8   
M1V                  2                      2                       2      2   
M1W                 11                     11                      11     11   
M2H                  2                      2                       2      2   
M2J                 28                     28                      28     28   
M2K                  3                      3                       3      3   
M2L                  1                      1                       1      1   
M2N                 23                     23                      23     23   
M2R                  3                      3                       3      3   
M3A                  2                      2                       2      2   
M3B                  4                      4                       4      4   
M3C                  9                      9                       9      9   
M3H                  9                      9                       9      9   
M3J                  4                      4                       4      4   
M3K                  1                      1                       1      1   
M3M                  2                      2                       2      2   
M4A                  4                      4                       4      4   
M4B                  7                      7                       7      7   
M4C                  4                      4                       4      4   
M4E                  3                      3                       3      3   
M4G                 21                     21                      21     21   
M4H                  8                      8                       8      8   
M4J                  3                      3                       3      3   
M4K                 38                     38                      38     38   
M4L                 11                     11                      11     11   
M4M                 27                     27                      27     27   
M4N                  1                      1                       1      1   
M4P                  4                      4                       4      4   
M4R                  8                      8                       8      8   
M4S                 30                     30                      30     30   
M4T                  2                      2                       2      2   
M4V                  9                      9                       9      9   
M4W                  1                      1                       1      1   
M4X                 29                     29                      29     29   
M4Y                 64                     64                      64     64   
M5A                 22                     22                      22     22   
M5B       

[To Top](#top)
<a name="mapping_restaurants"></a>
<h3>Mapping Restaurants</h3>

Earlier, we had a cell devoted to importing all of the things we need. Why is there one more import command here? We wanted to make a cool Folium map showing the locations of all our restaurants and we did make that map. Unfortunately, through some combination of using Jupyter notebook, the number of markers to be displayed, maybe even my laptop, we just get a blank map! Importing webbrowser will allow us to save our Folium map and open it in whatever browser.

In [26]:
import webbrowser

In [27]:
tor_rest_map = folium.Map(location=[latitude, longitude], zoom_start=12)

for code, latitude, longitude, venue, neighborhood in zip(tor_g['Postcode'],tor_g['Venue Latitude'], tor_g['Venue Longitude'], tor_g['Venue'], tor_g['Neighborhood']):
    label = 'Postcode: {}, Neighborhoods: {}, Restaurant: {}'.format(code, neighborhood, venue)
    folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [latitude, longitude],
        radius=4,
        popup=label,
        color='orange',
        fill=True,
        fill_color='blue',
        fill_opacity=0.8,
        parse_html=True).add_to(tor_rest_map)  

#if we don't comment this out, we can get a nice blank rectangle    
#tor_rest_map

We save our map and open it in a new tab. It looks pretty nice in fullscreen if I do say so myself.

In [28]:
tor_rest_map.save('restaurant_map.html')

In [29]:
webbrowser.open('restaurant_map.html', new=2)

True

[To Top](#top)
<a name="data"></a>
<a name="real_estate"></a>
<h3>Real Estate Heatmap</h3>

For one of our final pieces of data, we will be using a pre-existing heatmap from https://www.canadianbusiness.com/blogs-and-comment/check-out-this-heat-map-of-toronto-real-estate-prices/. We won't be able to see it in this notebook so off to the page we go!

**Some Possible Questions and Answers About The Heatmap**

**This heatmap is from 2013. Why not get a more current heatmap?**<br><br>
Try as I might, I could not find a more current one.

**Why not make a more current heatmap?**<br><br>
My Python is not the greatest at this time. I do have a geojson but I do not have the data on real estate prices sorted by the Forward Sortation Areas (FSA)/postcodes. I'm sure the data can be put together from somewhere but I'm quite behind on this project already with a report, presentation, and the rest of the notebook to finish. I may come back and create a heatmap in the future but for now, it's not happening.

**Why are you so behind?**<br><br>
This concludes our Q&A and our Data section.

[To Top](#top)
<a name="methodology"></a>
<h2>Methodology</h2>

We want to find a good location for the new buffet restaurant. We have our primary and secondary considerations so let's take another look at them before we do anything.

**Primary Consideration:** Are there other buffet restaurants nearby?

For our primary consideration, we found earlier that there were not that many buffet restaurants in Toronto.

**Secondary Consideration:** How many other restaurants are nearby?

For this secondary consideration, we will examine the number of restaurants in each neighborhood. We performed a group by postcode/FSA earlier and know the number of restaurants associated with each one. FSAs that have too many restaurants will be dropped from the running. I believe that a visual representation in the form of marked Choropleth maps of Toronto will be more effective here rather than filtering anything out.

**Secondary Consideration:** How much would it be to open in that location?

Should a clear recommendation not be possible at this point, we will do a side by side comparison of the restaurants Choropleth map and the real estate price heatmap.

<a name="competition"></a>
<h3>Secondary Consideration: How many other restaurants are nearby?</h3>

We have the tor_g dataframe which has information on over 1600 restaurants in Toronto. These restaurants are distributed through the many neighborhood areas. We need to figure out which areas have how many restaurants. A Choropleth map will allow us to determine if an area is to be rejected at a glance. The future buffet owner would like an area with fewer than 10 competing restaurants. We will use a geojson created using data from https://www12.statcan.gc.ca/census-recensement/2011/geo/bound-limit/bound-limit-2016-eng.cfm.

In [30]:
tor_g.head()

Postcode                       Neighborhood  Neighborhood Latitude  \
0      M1B                     Rouge, Malvern              43.806686   
1      M1B                     Rouge, Malvern              43.806686   
2      M1E  Guildwood, Morningside, West Hill              43.763573   
3      M1E  Guildwood, Morningside, West Hill              43.763573   
4      M1E  Guildwood, Morningside, West Hill              43.763573   

   Neighborhood Longitude                            Venue  Venue Latitude  \
0              -79.194353                          Wendy's       43.807448   
1              -79.194353               Meena's Fine Foods       43.804476   
2              -79.188711  Swiss Chalet Rotisserie & Grill       43.767697   
3              -79.188711                    Doug's Bakery       43.762400   
4              -79.188711                       Sail Sushi       43.765951   

   Venue Longitude        Venue Category  
0       -79.199056  Fast Food Restaurant  
1       -79.199753     Indian Restaurant  
2       -79.189914           Pizza Place  
3       -79.192285                Bakery  
4       -79.191275            Restaurant

We don't want all of this data so we'll just pull out what we want real quick.

In [31]:
tor_h = tor_g.groupby('Postcode').count()

unique_code = tor_g['Postcode'].unique()

n_venue = []
p_code = []

for x in range(len(tor_h)):
    n_venue.append(tor_h['Venue'][x])
    
for x in unique_code:
    p_code.append(x)
    
zipped = zip(p_code, n_venue)

post_venue = pd.DataFrame(zipped, columns=['Postcode','Count'])

post_venue

Postcode  Count
0       M1B      2
1       M1E      5
2       M1G      3
3       M1H      5
4       M1J      1
5       M1K      4
6       M1L      4
7       M1M      1
8       M1N      2
9       M1P      3
10      M1R      6
11      M1S      4
12      M1T      8
13      M1V      2
14      M1W     11
15      M2H      2
16      M2J     28
17      M2K      3
18      M2L      1
19      M2N     23
20      M2R      3
21      M3A      2
22      M3B      4
23      M3C      9
24      M3H      9
25      M3J      4
26      M3K      1
27      M3M      2
28      M4A      4
29      M4B      7
30      M4C      4
31      M4E      3
32      M4G     21
33      M4H      8
34      M4J      3
35      M4K     38
36      M4L     11
37      M4M     27
38      M4N      1
39      M4P      4
40      M4R      8
41      M4S     30
42      M4T      2
43      M4V      9
44      M4W      1
45      M4X     29
46      M4Y     64
47      M5A     22
48      M5B     91
49      M5C     76
50      M5E     50
51      M5G     68
52      M5H     95
53      M5J     82
54      M5K     97
55      M5L     98
56      M5M     20
57      M5P      4
58      M5R     15
59      M5S     29
60      M5T     57
61      M5V      2
62      M5W     97
63      M5X     97
64      M6A      3
65      M6B      5
66      M6E      1
67      M6G      7
68      M6H      9
69      M6J     45
70      M6K     14
71      M6L      2
72      M6M      5
73      M6N      4
74      M6P     15
75      M6R      7
76      M6S     26
77      M7A     28
78      M7R      6
79      M7Y      5
80      M8V     11
81      M8W      4
82      M8Y      2
83      M8Z      5
84      M9A      1
85      M9B      1
86      M9C      3
87      M9L      4
88      M9P      5
89      M9R      1
90      M9V      5

Let's get our Choropleth map fired up!

In [32]:
tor_rest_heatmap = folium.Map()

tor_geodata = r'Toronto_FSA.geojson'

tor_rest_heatmap = folium.Map(location=[latitude,longitude], zoom_start=12)
tor_rest_heatmap.choropleth(
    geo_data=tor_geodata,
    data=post_venue,
    columns=['Postcode','Count'],
    key_on='feature.properties.CFSAUID',
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='Restaurants In Toronto FSA/Postcode'
)

tor_rest_heatmap

C:\Users\Chris\Anaconda3\lib\site-packages\folium\folium.py:415: FutureWarning: The choropleth  method has been deprecated. Instead use the new Choropleth class, which has the same arguments. See the example notebook 'GeoJSON_and_choropleth' for how to do this.
  FutureWarning


**Heatmap**: https://i.imgur.com/LlQu3X0.jpg

Wow! Looks great and all the FSAs are clearly delineated. It's just too bad that we don't know which one is which. We'll fix that.

**There are some things of note.**

Some FSAs have no restaurants. They are dark.

Only the FSAs by the Billy Bishop Toronto City Airport in the south have a high concentration. Most everywhere else doesn't have too much in the way of other restaurants.

In [33]:
tor_fsa = folium.Map()

tor_fsa = folium.Map(location=[latitude,longitude], zoom_start=11)
tor_fsa.choropleth(
    geo_data=tor_geodata,
    data=post_venue,
    columns=['Postcode','Count'],
    key_on='feature.properties.CFSAUID',
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='Restaurants In Toronto FSA/Postcode'
)

for code, latitude, longitude in zip(postal_table_coord['Postcode'],postal_table_coord['Latitude'], postal_table_coord['Longitude']):
    label = 'Postcode: {}'.format(code)
    folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [latitude, longitude],
        radius=4,
        popup=label,
        color='green',
        fill=True,
        fill_color='green',
        fill_opacity=0.8,
        parse_html=True).add_to(tor_fsa)


In [34]:
tor_fsa.save('tor_fsa.html')

In [35]:
webbrowser.open('tor_fsa.html')

True

In [36]:
tor_fsa

**Heatmap with FSA Markers**: https://i.imgur.com/GxMj6Cs.jpg

Let's see what it's like with the restaurants marked on the heatmap.

In [37]:
tor_rest_heatmap_r = folium.Map()

tor_geodata = r'Toronto_FSA.geojson'

tor_rest_heatmap_r = folium.Map(location=[latitude,longitude], zoom_start=11)
tor_rest_heatmap_r.choropleth(
    geo_data=tor_geodata,
    data=post_venue,
    columns=['Postcode','Count'],
    key_on='feature.properties.CFSAUID',
    fill_color='YlOrRd', 
    fill_opacity=0.7, 
    line_opacity=0.2,
    legend_name='Restaurants In Toronto FSA/Postcode'
)

In [38]:
for code, latitude, longitude, venue, neighborhood in zip(tor_g['Postcode'],tor_g['Venue Latitude'], tor_g['Venue Longitude'], tor_g['Venue'], tor_g['Neighborhood']):
    label = 'Postcode: {}, Neighborhoods: {}, Restaurant: {}'.format(code, neighborhood, venue)
    folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [latitude, longitude],
        radius=4,
        popup=label,
        color='grey',
        fill=True,
        fill_color='blue',
        fill_opacity=0.8,
        parse_html=True).add_to(tor_rest_heatmap_r)


In [39]:
tor_rest_heatmap_r.save('restaurant_heatmap.html')

In [40]:
webbrowser.open('restaurant_heatmap.html', new=2)

True

Before we forget though, we need to add the buffet-tagged restaurants back in.

In [41]:
for code, latitude, longitude, venue, neighborhood in zip(tor_b['Postcode'],tor_b['Venue Latitude'], tor_b['Venue Longitude'], tor_b['Venue'], tor_b['Neighborhood']):
    label = 'Postcode: {}, Neighborhoods: {}, Restaurant: {}'.format(code, neighborhood, venue)
    folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [latitude, longitude],
        radius=6,
        popup=label,
        color='red',
        fill=True,
        fill_color='red',
        fill_opacity=0.8,
        parse_html=True).add_to(tor_rest_heatmap_r)

In [42]:
tor_rest_heatmap_r.save('restaurant_heatmap_buffet.html')

In [43]:
webbrowser.open('restaurant_heatmap_buffet.html')

True

**Restaurant Heatmap with Restaurant and Buffet Markers**: https://i.imgur.com/wArNiuE.jpg

There seems to be quite a few decent options for the new buffet location based on these marked heatmaps.

[To Top](#top)
<a name="price"></a>
<h3>Secondary Consideration: How much would it be to open in that area?</h3>

We have several heatmaps of Toronto showing the density of restaurants by FSA or postcode. A clear recommendation still cannot be made so we now move to looking at the real estate price heatmap. These heatmaps are apparently exclusive to invited readers and the most current publicly available ones I can find are from 2013. They are also images and not the actual interactive heatmaps. They may not be the most accurate now considering that it's been years since they were made. However, they will still be a good starting point.

These heatmap images are from https://www.canadianbusiness.com/blogs-and-comment/check-out-this-heat-map-of-toronto-real-estate-prices/. Direct links to each of the heatmap images are as follows.

**Real Estate Heatmap Image 1 (shows total price scale):** https://www.canadianbusiness.com/wp-content/uploads/2013/08/realestateheat1.jpg

**Real Estate Heatmap Image 2 (shows total price scale):** https://www.canadianbusiness.com/wp-content/uploads/2013/08/realestateheat2.jpg

**Real Estate Heatmap Image 3 (shows price per square foot):** https://www.canadianbusiness.com/wp-content/uploads/2013/08/realestateheat3.jpg

It's not that fun to look back and forth between two images and try to figure it out. It's not easy either, at least for me. We'll get some somewhat better images to look at. They're not that much better but they help a little.

**R1 - Choropleth with Restaurant Markers**: https://i.imgur.com/LlQu3X0.jpg

**R2 - Choropleth with Restaurant Markers and Real Estate Heatmap Image 1**: https://i.imgur.com/VcikphD.jpg

**B1 - Choropleth with Restaurant + Buffet Markers**: https://i.imgur.com/wArNiuE.jpg

**B2 - Choropleth with Restaurant + Buffet Markers and Real Estate Heatmap Image 1**: https://i.imgur.com/fnKLE3D.jpg


We can see that prices are very high starting from the center of Toronto. Radiating outwards, prices are significantly lower.

[To Top](#top)
<a name="results"></a>
<h2>Results and Discussion</h2>

After gathering all our data together and creating our visuals, we can see a few things. The total count of restaurants in all of Toronto was close to 1700. Out of the total count, there were 49 restaurants tagged with buffet according to the Foursquare API. A very large portion of these restaurants and buffets are concentrated in the southern part of Toronto, close to the Billy Bishop Toronto City Airport. Getting farther from the Billy Bishop Toronto City Airport, restaurants are fairly evenly spread out among the different FSAs. Many of these FSAs have restaurant counts in the single digits or very low double digits. Some FSAs have no restaurants at all. When comparing against real estate prices, there are many restaurants in more expensive areas closer to the center of Toronto although very few in the most expensive center of Toronto. For the most part, real estate pricing appears to be mostly uniform across Toronto except for the expensive center areas and small areas in the southwest of Toronto.

There are many FSAs that will satisfy the primary and secondary considerations.

***Primary Consideration***: Are there other buffet restaurants nearby? We do not want any buffet restaurants.

There are few buffet restaurants in Toronto with most being concentrated near the Billy Bishop Toronto City Airport and a few towards the center of Toronto. Excluding the south of Toronto where airport is located, there are no buffets in the outer FSAs of Toronto.

***Secondary Consideration***: How many other restaurants are nearby? We are okay with some competition but not too much in relative comparison to highest possible competition in Toronto.

Based on the Choropleth map, there are some FSAs with high restaurant density. These FSAs are already not to be considered as they do not satisfy the primary consideration of not having other buffet restaurants. For the remaining FSAs, all are of zero, very low or low restaurant density.

***Secondary Consideration***: How much would it be to open in that location? The buffet will open but if possible, a cheaper location is better.

The center of Toronto is very expensive. Part of the southwest is expensive compared to most everywhere else that is not the center.

***Recommendation***: Choose to open in an FSA based in Northwest Toronto or in East Toronto. Although this does not provide a definite location, it does narrow the areas to look at by a good amount. This also does not take into account reasons why an FSA may have no or few restaurants such as zoning laws or traffic in the area.

[To Top](#top)
<a name="conclusion"></a>
<h2>Conclusion</h2>

The goal here is to recommend possible locations for a new buffet restaurant in Toronto, Ontario, Canada. These locations would be recommended if they satisfied three considerations. The Foursquare API was used to retrieve relevant information on Toronto buffets and restaurants with calls made using Foursquare's defined keywords. A geojson file was created using QGIS and data from Statistics Canada. This geojson was then used to create choropleth maps. Combined with markers using the information from Foursquare, the primary consideration of other buffets and the secondary consideration of other restaurants was addressed. Finally, using an existing heatmap of real estate pricing in Toronto addressed the secondary consideration of area pricing.

The final FSA remains to be chosen by the future buffet owner themself after learning more about each FSA and the properties available in each.